In [2]:
import pandas as pd
import json
from phoenix.client import Client

# Params for local or remote Phoenix instance
local = True
if local is True:
    client = Client(base_url="http://localhost:6006")
else:
    client = Client() # will use environment variables for configuration

# Load the existing spans
spans_df = client.spans.get_spans_dataframe(project_name="final_assignment_template", start_time="2025-10-23")

In [3]:
# Load the source of truth
dataset_df = pd.read_json("../data/metadata.jsonl", lines=True)

In [4]:
# Filter by root agents
agents_df = spans_df[(spans_df.span_kind == 'AGENT') & (spans_df.parent_id.isna()) & (spans_df.status_code == 'OK')]

In [5]:
# Retrieve the right question and add the answer
agents_df["task"] = agents_df["attributes.input.value"].apply(json.loads).apply(lambda x : x["task"]).str.replace(r'\s*The mentionned file can be downloaded from.*$', '', regex=True)
agents_merged_df = pd.merge(agents_df,dataset_df,how="left",left_on="task", right_on="Question")

/var/folders/pj/v1zrqj1d10x9_1rd2njh_r_r0000gn/T/ipykernel_47327/3107371246.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  agents_df["task"] = agents_df["attributes.input.value"].apply(json.loads).apply(lambda x : x["task"]).str.replace(r'\s*The mentionned file can be downloaded from.*$', '', regex=True)


In [6]:
from phoenix.evals.evaluators import bind_evaluator, async_evaluate_dataframe
from evaluators import conciseness_evaluator
from scorer import question_scorer_wrapper as question_scorer

# Define the evaluator
conciseness_evaluator = bind_evaluator(evaluator=conciseness_evaluator, input_mapping={ "output": "attributes.output.value", "expected": "Final answer"})
question_scorer_eval = bind_evaluator(evaluator=question_scorer, input_mapping={ "output": "attributes.output.value", "expected": "Final answer"})
results_df = await async_evaluate_dataframe(agents_merged_df, evaluators=[conciseness_evaluator, question_scorer_eval])


Evaluating `Claus`
Calling tools:
[{'id': 'call_1', 'type': 'function', 'function': {'name': 'final_answer', 'arguments': 'Claus'}}] as a string.
Evaluating FINAL ANSWER: I am unable to complete this task because the provided Excel file link (https://agents-course-unit4-scoring.hf.space/files/7bd855d8-463d-4ed5-93ca-5fe35145f733) consistently returns a "404 Client Error: Not Found". Without access to the sales data, I cannot perform the required calculations. as a number.
String FINAL ANSWER: I am unable to complete this task because the provided Excel file link (https://agents-course-unit4-scoring.hf.space/files/7bd855d8-463d-4ed5-93ca-5fe35145f733) consistently returns a "404 Client Error: Not Found". Without access to the sales data I cannot perform the required calculations. cannot be normalized to number str.
Evaluating Okay, it seems there was an issue accessing the previous NPB link. Let's try another source for the Hokkaido Nippon-Ham Fighters' 2023 roster.

Taishō Tamai's numb

/Users/romainfayoux/Documents/Programmation/Final_Assignment_Template/eval/scorer.py:61: UserWarning: Answer lists have different lengths, returning False.
  warnings.warn(


Evaluating Saint Petersburg as a string.Evaluating **Paper Found:**

The paper mentioned in the Universe Today article "There Are Hundreds of Mysterious Filaments at the Center of the Milky Way" by Carolyn Collins Petersen, published on June 6, 2023, is:

"The Population of the Galactic Center Filaments: Position Angle Distribution Reveal a Degree-scale Collimated Outflow from Sgr A* along the Galactic Plane" by F. Yusef-Zadeh, R. G. Arendt, M. Wardle, and I. Heywood.

It is accessible on arXiv at: [https://arxiv.org/abs/2306.01071](https://arxiv.org/abs/2306.01071)

**NASA Award Number for R. G. Arendt:**

To find the NASA award number, I need to access the PDF version of the paper.
Accessing the PDF directly: [https://arxiv.org/pdf/2306.01071](https://arxiv.org/pdf/2306.01071)

Searching the "Acknowledgments" section of the paper, I found the following:

"The work of R. G. Arendt was supported by NASA award number **80GSFC21M0002**."

Therefore, the work performed by R. G. Arendt was

In [7]:
results_df["conciseness"] = results_df.conciseness_evaluator_score.apply(json.loads).apply(lambda x : x["label"])
results_df["question_scorer"] = results_df.question_scorer_score.apply(json.loads).apply(lambda x : x["score"])
results_df["agent_type"] = results_df["attributes.smolagents"].apply(lambda x : "multi_agent" if "managed_agents" in x else "llm_agent")
results_filtered_df = results_df[["name", "span_kind", "start_time", "context.span_id", "context.trace_id","attributes.output.value", "task_id", "Question", "Final answer", "agent_type", "conciseness_evaluator_score", "question_scorer_score", "conciseness", "question_scorer"]]

In [8]:
# Upload results
import numpy as np
from phoenix.evals.utils import to_annotation_dataframe

annotation_df = to_annotation_dataframe(results_filtered_df)
annotation_df = annotation_df.replace({np.nan: None})
client.spans.log_span_annotations_dataframe(dataframe=annotation_df)


/Users/romainfayoux/Documents/Programmation/Final_Assignment_Template/.venv/lib/python3.12/site-packages/phoenix/evals/utils.py:367: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  result_df = pd.concat(result_dfs, ignore_index=True)
